In [2]:
pip install spacy_sentiws

Note: you may need to restart the kernel to use updated packages.


In [2]:
import json
import pandas as pd
import aki_prj23_transparenzregister.utils.mongo.connector as conn
from aki_prj23_transparenzregister.config.config_providers import JsonFileConfigProvider
import aki_prj23_transparenzregister.utils.mongo.news_mongo_service as news
import aki_prj23_transparenzregister.utils.mongo.sentiment_service as sentiment_service
from tqdm import tqdm

ValueError: [E002] Can't find factory for 'sentiws' for language German (de). This usually happens when spaCy calls `nlp.create_pipe` with a custom component name that's not registered on the current language class. If you're using a Transformer, make sure to install 'spacy-transformers'. If you're using a custom component, make sure you've added the decorator `@Language.component` (for function components) or `@Language.factory` (for class components).

Available factories: attribute_ruler, tok2vec, merge_noun_chunks, merge_entities, merge_subtokens, token_splitter, doc_cleaner, parser, beam_parser, lemmatizer, trainable_lemmatizer, entity_linker, entity_ruler, tagger, morphologizer, ner, beam_ner, senter, sentencizer, spancat, spancat_singlelabel, span_finder, future_entity_ruler, span_ruler, textcat, textcat_multilabel

In [2]:
# Mongo Connect: create connection string and connect
config_provider = JsonFileConfigProvider("../../secrets.json")
engine = config_provider.get_mongo_connection_string()
connector = conn.MongoConnector(config_provider.get_mongo_connection_string())

In [3]:
# Read data from database
newsObj = news.MongoNewsService(connector)
allNews = newsObj.get_all()

# Create a cursor which has all unprogressed articles; articles without the attribute 'companies'
CursorUnprogressed = newsObj.collection.find({"sentiment": {"$exists": False}})
documents = list(CursorUnprogressed)

In [4]:
# documents.rewind()
docAttrib = "title"  # "title"

if len(documents) > 0:
    for document in tqdm(range(len(documents))):
        # ents=NERService.NERCompanyList(company_list,document)
        text = documents[document]["title"]
        # ents=SentimentService.SentimentSpacy(text)
        ents = sentiment_service.sentiment_transformer(text)

        # create a sentiment-attribute with label and score
        sentiment = {"label": ents[0], "score": ents[1]}
        # print(sentiment)
        # add a new attribute 'sentiment' to document
        # newsObj.collection.update_one(
        #        {"_id":  documents[document]["_id"]},  # Filter für das entsprechende Dokument
        #        {"$set": {"sentiment": sentiment}}  # add new attribute 'sentiment'
        #     )

else:
    print("No documents found.")

  0%|          | 0/1311 [00:00<?, ?it/s]

  4%|▍         | 53/1311 [00:24<09:31,  2.20it/s]


KeyboardInterrupt: 

In [22]:
documents

[]

In [101]:
CursorProgressed = newsObj.collection.find({"companies": {"$exists": True}})

In [102]:
docs = list(CursorProgressed)

In [103]:
docs

[{'_id': '08a99fad-b0be-4481-ac87-b71a8eeeb95e',
  'title': 'Siemens baut neue Hightech-Fabrik in Singapur',
  'date': '2023-06-15T19:23:48.142+02:00',
  'text': ' Der Siemens hat neue Investitionen in Milliardenhöhe angekündigt. Das Geld fließt in den Ausbau eines Werks in Zentralchina, aber auch in eine neue Hightech-Fabrik in Singapur. Ein Umdenken der Konzerns?   Siemens will in diesem Jahr zwei Milliarden Euro in Fabriken und Forschung in Asien, den USA und Europa investieren. Dabei soll es einen starken Fokus auf Asien geben: So werde in Zentralchina das Werk in Chengdu für 140 Millionen Euro ausgebaut, erklärte der Konzern. Gleichzeitig errichtet er in Singapur für 200 Millionen eine neue Hightech-Fabrik. An beiden Standorten werden so demnach jeweils 400 Arbeitsplätze entstehen.   In Chengdu will Siemens seine Produktionskapazitäten um 40 Prozent ausbauen. "Der chinesische Markt ist stark und wird weiter wachsen", sagte Vorstandschef\xa0Roland Busch dem "Handelsblatt". Kein Unt